## Predictions in Energy Economics - Examplary Household and PV Load Predictions ##

In [1]:
import pandas as pd
import numpy as np
import warnings
import plotly.graph_objects as go

from workalendar.europe import Germany
from sklearn.model_selection import TimeSeriesSplit
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score

warnings.filterwarnings("ignore")

From the Electric Load Profiles and Vehicle Data of Private Households with a Bidirectional EV open data one customer was selected. <br>
https://opendata.ffe.de/dataset/electric-load-profiles-and-vehicle-data-of-private-households-with-a-bidirectional-ev/ <br>
For this data the goal is to predict the Household and PV Load for the next day meaning 96 time steps. <br>
This notebook has the goal to be a simple example of time series predictions. For these predictions features are created, which rely solely on the time series. Hence, weather or other external data are not included as features despite them potentialy being important fatures for the predictions. <br><br>
First the csv is read in as a pandas DataFrame and the timestamps, which are first given as strings are translated to pandas Timestamp object. This has the advantage that later a lot of features can be read from the datetime objects. The columns apart from Power Household and Power PV will be dropped as they are not one of the target variables.

In [2]:
# read the .csv and transform it to a dataframe
customer_df = pd.read_csv('customer_6.csv')
customer_df['Timestamp'] = pd.to_datetime(customer_df['Timestamp UTC'])
customer_df.set_index('Timestamp',inplace=True)
customer_df['date'] = customer_df.index.date
customer_df.index = customer_df.index.tz_convert('Europe/Berlin')
customer_df.drop(['Customer ID', 'Power GCP', 'Power EVSE', 'Connection', 'SoC', 'Target SoC', 'Timestamp UTC'], axis=1, inplace=True)
customer_df.head()

Power PV  Power Household        date
Timestamp                                                       
2021-08-15 02:00:00+02:00 -1.287293       348.668528  2021-08-15
2021-08-15 02:15:00+02:00 -1.288492       265.796639  2021-08-15
2021-08-15 02:30:00+02:00 -1.328677       296.696012  2021-08-15
2021-08-15 02:45:00+02:00 -1.313963       238.116575  2021-08-15
2021-08-15 03:00:00+02:00 -1.291442       300.027456  2021-08-15

Pandas Timestamps are now utilized to generate time-of-day features, which will be transformed into cyclic cosine and sine features to represent the periodic nature of time during the day.<br> 
The same process is applied to time-of-year features to potentially capture seasonal trends, especially if multiple years of data are available. <br>
Additionally, dummy variables are introduced for weekdays; they are set to 1 for the current weekday and 0 for all other days. While it's possible to include dummy variables for time of day or year, this would lead to a substantially larger number of columns.<br>
Similarly, holidays are incorporated into the analysis.

In [3]:
customer_df['time_of_day'] = customer_df.index.hour + customer_df.index.minute / 60
customer_df['time_of_year'] = ((customer_df.index.dayofyear-1) * 24) + customer_df.index.hour + customer_df.index.minute / 60

# create cyclic deature for time_of_day and time_of_year
features_temp = ['time_of_day', 'time_of_year']
corr_numbers = [24, 8760]
for f, n in zip(features_temp, corr_numbers):
    customer_df[f + '_sin'] = np.sin(customer_df[f]*(2.*np.pi/n))
    customer_df[f + '_cos'] = np.cos(customer_df[f]*(2.*np.pi/n))

customer_df.drop(columns=['time_of_year'], inplace=True)

# create weekdays
customer_df['weekday'] = customer_df.index.weekday

# create dummies for weekdays
weekday_dummies = pd.get_dummies(customer_df["weekday"])
weekdays = [
    "Monday",
    "Tuesday",
    "Wednesday",
    "Thursday",
    "Friday",
    "Saturday",
    "Sunday",
]
for i in np.arange(7):
    customer_df[weekdays[i]] = weekday_dummies[i]

# now also holidays shall be added as features thus we first create a date feature
years = [2021, 2022]

holidays = pd.DataFrame(Germany().holidays(years[0]), columns=["date", "holiday"])
if len(years) > 1:
    for i in np.arange(1, len(years)):
        holidays = pd.concat([holidays,
            pd.DataFrame(Germany().holidays(years[i]), columns=["date", "holiday"])]
        )
customer_df["holiday"] = 0

for day in holidays.date:
    customer_df.loc[customer_df.date == day, "holiday"] = 1

customer_df.head()

Power PV  Power Household        date  time_of_day  \
Timestamp                                                                       
2021-08-15 02:00:00+02:00 -1.287293       348.668528  2021-08-15         2.00   
2021-08-15 02:15:00+02:00 -1.288492       265.796639  2021-08-15         2.25   
2021-08-15 02:30:00+02:00 -1.328677       296.696012  2021-08-15         2.50   
2021-08-15 02:45:00+02:00 -1.313963       238.116575  2021-08-15         2.75   
2021-08-15 03:00:00+02:00 -1.291442       300.027456  2021-08-15         3.00   

                           time_of_day_sin  time_of_day_cos  time_of_year_sin  \
Timestamp                                                                       
2021-08-15 02:00:00+02:00         0.500000         0.866025         -0.681823   
2021-08-15 02:15:00+02:00         0.555570         0.831470         -0.681955   
2021-08-15 02:30:00+02:00         0.608761         0.793353         -0.682086   
2021-08-15 02:45:00+02:00         0.659346         0.751840         -0.682217   
2021-08-15 03:00:00+02:00         0.707107         0.707107         -0.682348   

                           time_of_year_cos  weekday  Monday  Tuesday  \
Timestamp                                                               
2021-08-15 02:00:00+02:00         -0.731517        6       0        0   
2021-08-15 02:15:00+02:00         -0.731394        6       0        0   
2021-08-15 02:30:00+02:00         -0.731272        6       0        0   
2021-08-15 02:45:00+02:00         -0.731150        6       0        0   
2021-08-15 03:00:00+02:00         -0.731028        6       0        0   

                           Wednesday  Thursday  Friday  Saturday  Sunday  \
Timestamp                                                                  
2021-08-15 02:00:00+02:00          0         0       0         0       1   
2021-08-15 02:15:00+02:00          0         0       0         0       1   
2021-08-15 02:30:00+02:00          0         0       0         0       1   
2021-08-15 02:45:00+02:00          0         0       0         0       1   
2021-08-15 03:00:00+02:00          0         0       0         0       1   

                           holiday  
Timestamp                           
2021-08-15 02:00:00+02:00        0  
2021-08-15 02:15:00+02:00        0  
2021-08-15 02:30:00+02:00        0  
2021-08-15 02:45:00+02:00        0  
2021-08-15 03:00:00+02:00        0

In addition to the timestamp-specific features, lagged and mean features are incorporated. It's crucial to utilize only past data to avoid introducing information from the future. Lag values of $96$ time steps (representing the previous day) and $7 \times 96$ time steps (corresponding to the previous weeks at the same time) are selected, as they may exhibit similar behavior to the current time step.  <br><br>
Furthermore, the mean power is computed for the specific time and weekday, resulting in the '_time_wd_mean' column. However, for each data point, only past time steps are considered in this calculation. <br>
To efficiently carry out these operations, 'groupbys' are employed, requiring an equal number of time steps for each date. To achieve this uniformity, dates were standardized to UTC time, ensuring that each day contains an equal number of timestamps. All of these features are generated for both Power PV and Power Household targets.

In [4]:
target_list = ['Power PV', 'Power Household']
for target in ['Power PV', 'Power Household']:
    customer_df = customer_df[customer_df[f'{target}'].isna() == False]

    # add lagged features
    day_lag = 96
    week_lag = 7 * 96
    customer_df[f"{target}_day_lag"] = customer_df[target].shift(periods=day_lag)
    customer_df[f"{target}_week_lag"] = customer_df[target].shift(periods=week_lag)

    # add the same weekday and time means of previous time steps
    customer_df[f"{target}_time_wd_mean"] = np.nan
    customer_df.sort_index(inplace=True)
    i = 0
    for date in customer_df.date.unique():
        if i > 6:
            weekday = date.weekday()
            temp_df = customer_df[(customer_df.date < date) & (customer_df.weekday == weekday)]

            customer_df.sort_values(by=['time_of_day'], inplace=True)
            temp_df.sort_values(by=['time_of_day'], inplace=True)

            if len(temp_df.groupby(['time_of_day'])[target].mean().values) == len(
                customer_df.loc[customer_df.date == date, f"{target}_time_wd_mean"]
            ):
                customer_df.loc[customer_df.date == date, f"{target}_time_wd_mean"] = (
                    temp_df.groupby(['time_of_day'])[target].mean().values
                )
        i += 1
    customer_df.sort_index(inplace=True)

# to avoid NaNs, the timesteps were the lags and means could not be provided are dropped
customer_df = customer_df[customer_df[f'{target}_time_wd_mean'].isna() == False]
customer_df.head()

Power PV  Power Household        date  time_of_day  \
Timestamp                                                                       
2021-08-22 02:00:00+02:00 -1.400356       218.718773  2021-08-22         2.00   
2021-08-22 02:15:00+02:00 -1.423189       211.155597  2021-08-22         2.25   
2021-08-22 02:30:00+02:00 -1.444197       160.401048  2021-08-22         2.50   
2021-08-22 02:45:00+02:00 -1.448730       183.258847  2021-08-22         2.75   
2021-08-22 03:00:00+02:00 -1.456320       222.623531  2021-08-22         3.00   

                           time_of_day_sin  time_of_day_cos  time_of_year_sin  \
Timestamp                                                                       
2021-08-22 02:00:00+02:00         0.500000         0.866025         -0.764814   
2021-08-22 02:15:00+02:00         0.555570         0.831470         -0.764929   
2021-08-22 02:30:00+02:00         0.608761         0.793353         -0.765045   
2021-08-22 02:45:00+02:00         0.659346         0.751840         -0.765160   
2021-08-22 03:00:00+02:00         0.707107         0.707107         -0.765275   

                           time_of_year_cos  weekday  Monday  ...  Friday  \
Timestamp                                                     ...           
2021-08-22 02:00:00+02:00         -0.644252        6       0  ...       0   
2021-08-22 02:15:00+02:00         -0.644114        6       0  ...       0   
2021-08-22 02:30:00+02:00         -0.643977        6       0  ...       0   
2021-08-22 02:45:00+02:00         -0.643840        6       0  ...       0   
2021-08-22 03:00:00+02:00         -0.643703        6       0  ...       0   

                           Saturday  Sunday  holiday  Power PV_day_lag  \
Timestamp                                                                
2021-08-22 02:00:00+02:00         0       1        0         -1.376521   
2021-08-22 02:15:00+02:00         0       1        0         -1.401616   
2021-08-22 02:30:00+02:00         0       1        0         -1.384809   
2021-08-22 02:45:00+02:00         0       1        0         -1.470356   
2021-08-22 03:00:00+02:00         0       1        0         -1.454040   

                           Power PV_week_lag  Power PV_time_wd_mean  \
Timestamp                                                             
2021-08-22 02:00:00+02:00          -1.287293              -1.287293   
2021-08-22 02:15:00+02:00          -1.288492              -1.288492   
2021-08-22 02:30:00+02:00          -1.328677              -1.328677   
2021-08-22 02:45:00+02:00          -1.313963              -1.313963   
2021-08-22 03:00:00+02:00          -1.291442              -1.291442   

                           Power Household_day_lag  Power Household_week_lag  \
Timestamp                                                                      
2021-08-22 02:00:00+02:00               340.516520                348.668528   
2021-08-22 02:15:00+02:00               456.640890                265.796639   
2021-08-22 02:30:00+02:00               310.813206                296.696012   
2021-08-22 02:45:00+02:00               186.146761                238.116575   
2021-08-22 03:00:00+02:00               153.747945                300.027456   

                           Power Household_time_wd_mean  
Timestamp                                                
2021-08-22 02:00:00+02:00                    348.668528  
2021-08-22 02:15:00+02:00                    265.796639  
2021-08-22 02:30:00+02:00                    296.696012  
2021-08-22 02:45:00+02:00                    238.116575  
2021-08-22 03:00:00+02:00                    300.027456  

[5 rows x 23 columns]

The data is now split into training and testing sets. While for non-time series data, random data points can be used, in the case of time series data, it can be highly beneficial to have knowledge of future data. Consequently, assessing the model's performance on the testing data in a straightforward manner could be misleading. To address this, the last 10% of the data is reserved for testing, and predictions are made for data that lies in the future relative to the model, simulating a real-world application scenario.<br><br>

Typically, the data would be further subdivided into a validation set, which would be employed for hyperparameter tuning using methods such as grid search. However, for the sake of simplicity, this additional step is omitted in this context.

In [5]:
forecast_period = 96
train_ratio = 0.9
n = len(customer_df)
test_offset = (n - int(n * train_ratio)) % forecast_period
test_index = int(n * train_ratio) - (forecast_period - test_offset)

train = customer_df[:test_index]
test = customer_df[test_index:]

fig = go.Figure()
fig.add_trace(go.Scatter(x=train.index, y= train['Power PV'], name = 'Train PV'))
fig.add_trace(go.Scatter(x=test.index, y= test['Power PV'], name = 'Test PV'))
fig.add_trace(go.Scatter(x=train.index, y= train['Power Household'], name = 'Train Household'))
fig.add_trace(go.Scatter(x=test.index, y= test['Power Household'], name = 'Test Household'))
fig.update_yaxes(title= 'Power in W')
fig.show()

In order to initially assess the suitability of different features, a correlation analysis is conducted. <br>
This analysis generates a matrix that illustrates the degree of linear dependence between each variable within the data frame. This information can be used to identify specific features with the strongest correlations or anti-correlations. <br>
Additionally, when two features exhibit a high level of correlation (greater than 0.95), it may be advisable to exclude one of them since their behavior is so similar.

In [6]:
corr = train.corr()
corr.style.background_gradient(cmap="coolwarm")

Two methods are selected for the prediction: Linear Regression and Random Forest. <br>
It's important to note that the use of Linear Regression and Random Forest does not necessarily imply that they are the optimal choices for this time series analysis. However, these methods are considered applicable, and additional insights into method selection can be found at the following link: https://www.ffe.de/en/publications/predictions-in-energy-economics-which-methods-are-suitable/. <br>
Here, the default configurations of these methods are employed. Specifically, for Random Forest, this entails using 100 trees and continuing to create splits until fewer than 2 samples support further separation. <br><br>
This prediction process will be conducted in two distinct approaches. <br>
Firstly, the entire testing period is predicted in a single step without retraining the models. <br>
Secondly, the prediction is performed in a walk-forward manner, where the models are retrained at the end of each day. It's worth noting that the walk-forward method, due to its frequent retraining, requires significantly more time to complete. But the inclusion of the most recent data can lead to improved forecasting.

In [7]:
# Predict the entire test period in a single step.
# to later compare the predictions they are safed in pred_df.
pred_df = pd.DataFrame(index = test.index)

for target in target_list:
    # the selection of features, here also different combinations can be tested
    features = [*weekdays, f"{target}_day_lag", f"{target}_week_lag", f"{target}_time_wd_mean", 'holiday', 'time_of_day_sin', 'time_of_day_cos', 'time_of_year_sin', 'time_of_year_cos']

    model_LinR = LinearRegression()
    # by selecting the number of jobs the level of parallelization can be chosen
    model_RF = RandomForestRegressor(n_jobs = 8)

    # train on the training period
    model_LinR_fit = model_LinR.fit(train[features], train[target])
    model_RF_fit = model_RF.fit(train[features], train[target])

    pred_df[target] = test[target]
    # make and safe the predictions
    pred_df[f'{target}_pred_LinR'] = model_LinR_fit.predict(test[features])
    pred_df[f'{target}_pred_RF'] = model_RF_fit.predict(test[features])

In [8]:
# Predict the test period in a walk-forward manner
# define pred_df here if the previous cell wasn't executed yet
# pred_df = pd.DataFrame(index = test.index)

for target in target_list:
    print(f'{target}')
    # the selection of features, here also different combinations can be tested
    features = [*weekdays, f"{target}_day_lag", f"{target}_week_lag", f"{target}_time_wd_mean", 'holiday', 'time_of_day_sin', 'time_of_day_cos', 'time_of_year_sin', 'time_of_year_cos']

    # split time series in training and testing to employ the walk forward method
    tscv_test = TimeSeriesSplit(gap=0, test_size=forecast_period, n_splits=int(len(test) / forecast_period))

    model_LinR = LinearRegression()
    # by selecting the number of jobs the level of parallelization can be chosen
    model_RF = RandomForestRegressor(n_jobs = 8)
    
    pred_LinR = []
    pred_RF = []

    length = int(len(test) / 96)

    i= 1
    for train_index, test_index in tscv_test.split(customer_df):
        # print a progress bar
        arrow = '=' * int(i)
        spaces = ' ' * (length - len(arrow))
        print(f'\r[{arrow + spaces}] {int((i/length) * 100)}%', end='', flush=True)

        # train until the previous day
        model_LinR_fit = model_LinR.fit(customer_df[features].iloc[train_index], customer_df[target].iloc[train_index])
        model_RF_fit = model_RF.fit(customer_df[features].iloc[train_index], customer_df[target].iloc[train_index])

        # make and safe the predictions
        pred_LinR.append(model_LinR_fit.predict(customer_df[features].iloc[test_index]))
        pred_RF.append(model_RF_fit.predict(customer_df[features].iloc[test_index]))
        i += 1
        
    print('\n')
    # pred_df[target] = test[target]
    pred_df[f'{target}_pred_LinR_WF'] = [y for x in pred_LinR for y in x]
    pred_df[f'{target}_pred_RF_WF'] = [y for x in pred_RF for y in x]


Power PV
[=====================================] 100%

Power Household
[=====================================] 100%



To compare the predictions of the differen methods, three error metrics are calculated with $N$ the number of predicted values, $y_i$ the real values and $\hat{y}_i$ the prediction:
$$ \text{RMSE} =  \sqrt{\frac{1}{N} \sum_{i=0}^N (\hat{y}_i-y_i )^2 }$$
$$ \text{MAE}  = \frac{1}{N} \sum_{i=0}^N |\hat{y}_i-y_i| $$
$$ \text{R}^2 = 1 - \frac{\sum_{i=0}^N (\hat{y}_i-y_i )^2}{\sum_{i=0}^N (\bar{y}-y_i )^2} $$
Further information about error metrics can be found here: https://www.ffe.de/en/publications/predictions-in-energy-economics-which-error-metrics-are-suitable/.

In [9]:
metrics_df = pd.DataFrame()

for target in target_list:
    metrics_df_temp = pd.DataFrame()
    for method in ['LinR', 'LinR_WF', 'RF', 'RF_WF']:
        metrics_df_temp[f'target'] = [target]
        metrics_df_temp[f'method'] = [method]
        metrics_df_temp[f'RMSE'] = [mean_squared_error(pred_df[target], pred_df[f'{target}_pred_{method}'], squared= False)]
        metrics_df_temp[f'MAE'] = [mean_absolute_error(pred_df[target], pred_df[f'{target}_pred_{method}'])]
        metrics_df_temp[f'R2'] = [r2_score(pred_df[target], pred_df[f'{target}_pred_{method}'])]
        metrics_df = metrics_df.append(metrics_df_temp)

metrics_df

target   method        RMSE         MAE        R2
0         Power PV     LinR  980.975835  597.129970  0.793216
0         Power PV  LinR_WF  980.396671  594.084242  0.793460
0         Power PV       RF  952.066561  528.830846  0.805224
0         Power PV    RF_WF  965.084373  525.934426  0.799861
0  Power Household     LinR  559.659013  373.833778  0.014237
0  Power Household  LinR_WF  554.713892  358.918162  0.031580
0  Power Household       RF  558.630230  317.321012  0.017857
0  Power Household    RF_WF  561.992411  330.213644  0.006000

Finally, also a visual representation of the different predictions and the true values is given. <br>
The different variables can be toggled on and off by clicking on their legend. Furthermore, one can also zoom into the plot to make more detailed observations.

In [10]:
for target in target_list:
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=pred_df.index, y= pred_df[target], name= f'{target}'))
    fig.add_trace(go.Scatter(x=pred_df.index, y= pred_df[f'{target}_pred_LinR'], name= 'LinR'))
    fig.add_trace(go.Scatter(x=pred_df.index, y= pred_df[f'{target}_pred_RF'], name= 'RF'))
    fig.add_trace(go.Scatter(x=pred_df.index, y= pred_df[f'{target}_pred_LinR_WF'], name= 'LinR WF'))
    fig.add_trace(go.Scatter(x=pred_df.index, y= pred_df[f'{target}_pred_RF_WF'], name= 'RF WF'))
    fig.update_yaxes(title= 'Power in W')
    fig.show()